In [1]:
from bs4 import BeautifulSoup
import pandas as pd
import seaborn as sns
import requests
import re
import datetime as dt

## Grabbing Season Per Game Data

In [ ]:
# NBA seasons I am planning on analyzing (2014-15 season to 2018-19 season)
years = [year for year in range(2017,2020)]

# URL pages that I want to scrape:
# will be for years between 2015 and 2019, but I am inputting 2019, just as a test season
year = 2019

season_url = f'https://www.basketball-reference.com/leagues/NBA_{year}_per_game.html'

season_html = requests.get(season_url).text

season_soup = BeautifulSoup(season_html, 'lxml')

In [ ]:
# grabbing column headers

# headers = season_soup.find('table', id='per_game_stats').find('thead').find_all('th')

headers = season_soup.find('thead').find_all('th')

header_list = [th.text for th in headers]

# we don't need the rank column, so we will drop it
header_list = header_list[1:]

header_list

In [ ]:
# grabbing row data from cells
rows = season_soup.find_all('tr')[1:]
season_stats = [[td.text for td in rows[i].find_all('td')] for i in range(len(rows))]
season_stats

In [ ]:
season_stats = pd.DataFrame(season_stats, columns=header_list)

season_stats

In [ ]:
# checking number of unique players throughout the season
len(season_stats['Player'].unique())

In [ ]:
# Player data with multiple teams indicate that they were traded during the season
# we want the TOT stats, as they are the average across all games for all teams the player played on

traded_players = season_stats[season_stats['Tm']=='TOT']

traded_players

In [ ]:
# list of traded players
traded_list = [player for player in traded_players['Player']]

# remove all rows of players in traded list
season_stats = season_stats[~season_stats['Player'].isin(traded_list)]

# season_stats.drop_duplicates(subset='Player', keep='first')
season_stats = pd.concat([season_stats,traded_players])

In [ ]:
# checking for any extra duplicated rows
season_stats.duplicated().values.any()

### Function: Player Averages Over A Season

2019 indicates NBA season 2018-19

In [2]:
# putting everything into a single function

def season_per_game(year):

    season_html = requests.get(f'https://www.basketball-reference.com/leagues/NBA_{year}_per_game.html').text

    season_soup = BeautifulSoup(season_html, 'lxml')

    # grabbing column headers

    headers = season_soup.find('thead').find_all('th')
    
    # we don't need the rank column, so we will drop it
    header_list = [th.text for th in headers][1:]

    # grabbing row data from cells
    rows = season_soup.find_all('tr')[1:]
    season_stats = [[td.text for td in rows[i].find_all('td')] for i in range(len(rows))]

    # converting row data to dataframe
    season_stats = pd.DataFrame(season_stats, columns=header_list)

    # getting df with traded players based on team

    traded_players = season_stats[season_stats['Tm']=='TOT']

    # list of traded players
    traded_list = [player for player in traded_players['Player']]

    # remove all rows of players in traded list
    season_stats = season_stats[~season_stats['Player'].isin(traded_list)]

    # concatenating non-traded players, and traded players
    # dropping all team duplicates & resetting index
    return pd.concat([season_stats,traded_players]).drop_duplicates().dropna().reset_index().drop(columns='index')

In [ ]:
pd.set_option("display.max_rows", None, "display.max_columns", None)

In [ ]:
season_2018 = season_per_game(2018)

season_2018

In [ ]:
season_2019 = season_per_game(2019)

season_2019

In [3]:
def season_adv(year):

    season_adv_html = requests.get(f'https://www.basketball-reference.com/leagues/NBA_{year}_advanced.html').text

    season_adv_soup = BeautifulSoup(season_adv_html, 'lxml')

    # grabbing column headers

    headers = season_adv_soup.find('thead').find_all('th')
    
    # we don't need the rank column, so we will drop it
    header_list = [th.text for th in headers][1:]

    # grabbing row data from cells
    rows = season_adv_soup.find_all('tr')[1:]
    season_adv_stats = [[td.text for td in rows[i].find_all('td')] for i in range(len(rows))]

    # converting row data to dataframe
    season_adv_stats = pd.DataFrame(season_adv_stats, columns=header_list)

    # getting df with traded players based on team

    traded_players = season_adv_stats[season_adv_stats['Tm']=='TOT']

    # list of traded players
    traded_list = [player for player in traded_players['Player']]

    # remove all rows of players in traded list
    season_adv_stats = season_adv_stats[~season_adv_stats['Player'].isin(traded_list)]

    # concatenating non-traded players, and traded players
    # dropping all team duplicates & resetting index
    return pd.concat([season_adv_stats,traded_players]).drop_duplicates().dropna().reset_index().drop(columns='index')

In [ ]:
season_adv_2019 = season_adv(2019)

season_adv_2019

In [4]:
def adv_shooting(year):

    adv_shooting_html = requests.get(f'https://www.basketball-reference.com/leagues/NBA_{year}_shooting.html').text

    adv_shooting_soup = BeautifulSoup(adv_shooting_html, 'lxml')

    # grabbing column headers

    headers = adv_shooting_soup.find('thead').find('tr', class_= lambda x: x !='over_header').find_all('th')
    
    # we don't need the rank column, so we will drop it
    header_list = [th.text for th in headers][1:]

    # grabbing row data from cells
    rows = adv_shooting_soup.find_all('tr')[1:]
    adv_shooting_stats = [[td.text for td in rows[i].find_all('td')] for i in range(len(rows))]

    # converting row data to dataframe
    adv_shooting_stats = pd.DataFrame(adv_shooting_stats, columns=header_list)

    # getting df with traded players based on team

    traded_players = adv_shooting_stats[adv_shooting_stats['Tm']=='TOT']

    # list of traded players
    traded_list = [player for player in traded_players['Player']]

    # remove all rows of players in traded list
    adv_shooting_stats = adv_shooting_stats[~adv_shooting_stats['Player'].isin(traded_list)]

    # concatenating non-traded players, and traded players
    # dropping all team duplicates & resetting index
    adv_shooting_stats = pd.concat([adv_shooting_stats,traded_players]).drop_duplicates().dropna().reset_index().drop(columns='index')
    
    
    adv_shooting_stats = adv_shooting_stats.iloc[:,0:15].drop(columns = ['Pos', 'Age', 'Tm', 'G', 'MP', 'FG%'])
    
#     for column_name in list(adv_shooting_stats.columns):
#         adv_shooting_stats.rename(columns={column_name : '% ' + column_name})

    new_names = [(i,'%'+i) for i in adv_shooting_stats.iloc[:, 3:].columns.values]
    adv_shooting_stats.rename(columns = dict(new_names), inplace=True)
        
#     adv_shooting_stats.columns[2:9] = ['%' + str(col) for col in adv_shooting_stats.columns[2:9]]
    
    return adv_shooting_stats

#     return adv_shooting_stats.columns[2:9]

In [ ]:
adv_shooting_2017 = adv_shooting(2019)
adv_shooting_2017

In [ ]:
adv_shooting_2017.dtypes

## Grabbing Individual Player Attributes (Height, Weight)

In [ ]:
players_2018 = list(season_per_game(2018)['Player'])

len(players_2018)

In [ ]:
# plan: search for player id number based on player name
player = 'Jaylen Adams'

player_info_tag = season_soup.find('td', string=player)

player_id = player_info_tag['data-append-csv']

player_id

# retrieve player info on individual page based on id

In [5]:
# generates a dictionary of player names & id's based on season dataframe
def player_id_dict_generator(df,year):
# search for player id number based on player name
    player_id_dict = {}
    player_list = list(df['Player'])
    
    season_html = requests.get(f'https://www.basketball-reference.com/leagues/NBA_{year}_per_game.html').text

    season_soup = BeautifulSoup(season_html, 'lxml')
    
    
    for player in player_list:
#         player_info_tag = season_soup.find('td', attr={"data-stat":"player"})
        player_info_tag = season_soup.find('td', string=player)
        player_id = player_info_tag['data-append-csv']
        player_id_dict[player]=player_id.strip()

    return player_id_dict

In [ ]:
player_id_2018 = player_id_dict_generator(season_2018, 2018)

In [ ]:
player_id_2018

In [6]:
def height_to_inches(height):
    return int(height[0])*12 + int(height[2::])

In [7]:
# grabs individual player height & weight according to webpage ID
def player_ht_wt(player, player_id):
    player_html = requests.get(f'https://www.basketball-reference.com/players/{player_id[0]}/{player_id}.html').text
    
    soup = BeautifulSoup(player_html, 'lxml')
    
    headers = ['Player','player_id', 'Height', 'Weight']
    
    # check if player page html exists
    if len(soup)!=0:       
#         plyr_name = soup.find('h1', attrs={"itemprop":"name"}).find('span').text
        plyr_height = height_to_inches(soup.find('span', attrs={"itemprop":"height"}).text)
        plyr_weight = int(soup.find('span', attrs={"itemprop":"weight"}).text[:3])

        player_dict = dict(zip(headers, [player, player_id, plyr_height, plyr_weight]))

        
    else:
        player_dict = dict(zip(headers, [player, player_id, None, None]))
    
    return player_dict

In [ ]:
# showcases what happens to height & weight columns for player pages
# with len(html) == 0
player_ht_wt('Damian Jones','jonesda03')

In [8]:
import time
# combines all player metadata dictionaries into a list
def player_ht_wt_looper(id_list):
    player_ht_wt_list = []
    
    for player,player_id in id_list.items():
        player_attrib = player_ht_wt(player,player_id)
        player_ht_wt_list.append(player_attrib)
#         time.sleep(3)
        
#     for i, player_id in enumerate(id_list):
#         player_attrib = player_ht_wt(player_id)
#         player_ht_wt_list.append(player_attrib)
        
#         if (i+1%3 == 0):
#             time.sleep(3)
        
        
    return player_ht_wt_list

In [ ]:
player_ht_wt_looper(player_id_2019)

In [ ]:
player_test_html = requests.get('https://www.basketball-reference.com/players/j/jonesda03.html').text
test_soup = BeautifulSoup(player_test_html, 'lxml')

if len(test_soup)!=0:
    print("worked!")
    print(len(test_soup))
    
else:
    print('nope!')

In [ ]:
url = 'https://www.basketball-reference.com/robots.txt'

response = requests.get(url)
print(response.text)

In [ ]:
# converting the list of dictionaries into a dataframe
pd.DataFrame(players_5_2019)

### Function: Creating Player Metadata DF

In [9]:
def player_metadata(player_df,year):
    # creates a dictionary of player names & id's based on season dataframe
    player_id_dict = player_id_dict_generator(player_df,year)
    
    # grabs height and weight based on id value
    player_md_list = player_ht_wt_looper(player_id_dict)
    
    # creates dataframe of player id, matched with height & weight
    player_md_df = pd.DataFrame(player_md_list)
    
    return player_md_df

In [ ]:
metadata_2019 = player_metadata(season_2019,2019)

In [ ]:
metadata_2019

In [10]:
def player_webpage_checker(player_id_dict):
    failed=[]
    for player, player_id in player_id_dict.items():
        player_page_html = requests.get(f'https://www.basketball-reference.com/players/{player_id[0]}/{player_id}.html')
        if player_page_html.status_code!=200:
            failed.append(player_id)
    return failed

In [ ]:
player_webpage_checker()

### Function: Combining All DataFrames by Player

In [11]:
def df_combiner(df1, df2):
    return pd.merge(left=df1, right=df2, how='left', 
             left_on='Player', right_on='Player')

In [ ]:
season_2019_combined = df_combiner(season_2019, metadata_2019)

In [ ]:
season_2019_combined

In [12]:
def single_season_combined(year):
    # creating dataframe for per game data
    season_per_game_df = season_per_game(year)
    
    # creating dataframe for season advanced stats
    season_adv_df = season_adv(year).drop(columns = ['Pos', 'Age', 'Tm', 'G', 'MP'])
    
    # creating dataframe for player metadata
    player_metadata_df = player_metadata(season_per_game_df,year)
    
    adv_shooting_df = adv_shooting(year)
    
    # combining all dataframes

    player_stats_df = df_combiner(season_per_game_df, season_adv_df)
    player_stats_df = df_combiner(player_stats_df, player_metadata_df)
    player_stats_df = df_combiner(player_stats_df, adv_shooting_df)
    
#     return df_combiner(player_stats_df, player_metadata_df)

    return player_stats_df.drop(columns=['\xa0_x', '\xa0_y'])

In [ ]:
combined_df_2017 = single_season_combined(2017)

combined_df_2017

In [ ]:
combined_df_2017.columns

In [ ]:
combined_df_2017.dtypes

In [ ]:
combined_df_2017.columns[41]

In [ ]:
combined_df_2017.columns[46]

In [ ]:
combined_df_2017.columns[55]

In [ ]:
combined_df_2017.drop(columns=['\xa0_x', '\xa0_y'])

In [ ]:
combined_df_2018 = single_season_combined(2018)

combined_df_2018

In [ ]:
combined_df_2019 = single_season_combined(2019)
combined_df_2019

In [13]:
def multiple_seasons_combined(year_list):
    dfs = []
    for year in year_list:
        df = single_season_combined(year)
        
        dfs.append(df)
        
        
    return pd.concat(dfs).reset_index()

In [15]:
multiple_df = multiple_seasons_combined([2017,2018,2019])

In [ ]:
# to make sure that multiple years are included in the dataset
multiple_df['Player'].duplicated().any()

In [ ]:
multiple_df

In [ ]:
multiple_df.shape

In [31]:
def df_cleaner(df):
    final_df=df
#     final_df = df[['Player','Pos','Age','Height', 'Weight', 'MP', 'FGA', '3PA', '2PA', 
#                    'FTA','PTS', 'USG%', 'G']]
    
    final_df['G'] = final_df['G'].astype(int)
    final_df['Games_Missed'] = 82 - final_df['G']
    final_df['Pct_Games_Missed'] = final_df['Games_Missed']/82

#     final_df['Age']
    
    for column in list(final_df.columns[2:]):
        final_df[column] = pd.to_numeric(final_df[column], errors='ignore')
    
    # adding a bmi column      
#     final_df.insert(5, 'BMI', (final_df['Weight'] * 703) / (final_df['Height']**2))
    
    final_df['BMI'] = (final_df['Weight'] * 703) / (final_df['Height']**2)
    final_df['0-3_A'] = final_df['%0-3']*final_df['FGA']
    final_df['3-10_A'] = final_df['%3-10']*final_df['FGA']
    final_df['10-16_A'] = final_df['%10-16']*final_df['FGA']
    final_df['16-3P_A'] = final_df['%16-3P']*final_df['FGA']
    
    final_df = final_df.drop(columns=['index'])
    
#     return final_df = final_df[final_df['Height'].notna()]

    return final_df.dropna(subset=['Height', 'Weight']).reset_index(drop=True).fillna(0)

In [32]:
NBA_final_df = df_cleaner(multiple_df)

# final_df = final_df.reset_index(drop=True).drop(columns=['index'])

NBA_final_df

Player    Pos  Age   Tm        BMI   G  GS    MP  \
0                 Álex Abrines     SG   23  OKC  23.109796  68   6  15.5   
1                 Steven Adams      C   23  OKC  27.042386  80  80  29.9   
2                Arron Afflalo     SG   31  SAC  24.899646  61  45  25.9   
3                Alexis Ajinça      C   28  NOP  23.572742  39  15  15.0   
4                 Cole Aldrich      C   28  MIN  25.511685  62   0   8.6   
5            LaMarcus Aldridge     PF   31  SAS  25.511685  72  72  32.4   
6                  Lavoy Allen     PF   27  IND  27.858558  61   5  14.3   
7                   Tony Allen     SG   35  MEM  25.924342  71  66  27.0   
8              Al-Farouq Aminu     PF   26  POR  24.165625  61  25  29.1   
9               Chris Andersen      C   38  CLE  25.614961  12   0   9.5   
10               Alan Anderson     SF   34  LAC  25.420776  30   0  10.3   
11               Kyle Anderson     SF   23  SAS  24.644109  72  14  14.2   
12               Ryan Anderson     PF   28  HOU  25.715592  72  72  29.4   
13       Giannis Antetokounmpo     SF   22  MIL  24.695311  80  80  35.6   
14             Carmelo Anthony     SF   32  NYK  26.808845  74  74  34.3   
15                Joel Anthony      C   34  SAS  26.251334  19   0   6.4   
16                Trevor Ariza     SF   31  HOU  23.616406  80  80  34.7   
17              Darrell Arthur     PF   28  DEN  25.179851  41   7  15.6   
18                   Ömer Aşık      C   30  NOP  25.406037  31  19  15.5   
19               D.J. Augustin     PG   29  ORL  25.520532  78  20  19.7   
20                Luke Babbitt     SF   27  MIA  24.108368  68  55  15.7   
21                   Ron Baker     SG   23  NYK  26.776316  52  13  16.5   
22                Wade Baldwin     PG   20  MEM  24.342105  33   1  12.3   
23             Leandro Barbosa     SG   34  PHO  24.245689  67   0  14.4   
24                  J.J. Barea     PG   32  DAL  25.824490  35   6  22.0   
25             Harrison Barnes     PF   24  DAL  24.714844  79  79  35.5   
26                 Will Barton     SG   26  DEN  20.914366  60  19  28.4   
27                Brandon Bass     PF   31  LAC  27.460938  52   0  11.1   
28               Nicolas Batum     SG   28  CHO  25.264063  77  77  34.0   
29              Jerryd Bayless     PG   28  PHI  24.995556   3   1  23.7   
30                 Aron Baynes      C   30  DET  27.183224  75   2  15.5   
31               Kent Bazemore     SF   27  ATL  23.733553  73  64  26.9   
32                Bradley Beal     SG   23  WAS  25.870400  77  77  34.9   
33               Malik Beasley     SG   20  DEN  22.759868  22   1   7.5   
34             Michael Beasley     PF   28  MIL  25.179851  56   6  16.7   
35             Marco Belinelli     SG   30  CHO  26.085343  74   0  24.0   
36             DeAndre' Bembry     SF   22  ATL  24.899646  38   1   9.8   
37               Dragan Bender     PF   19  PHO  22.417092  43   0  13.3   
38             Anthony Bennett     PF   23  BRK  26.911719  23   1  11.5   
39                  Ben Bentil     PF   21  DAL  25.179851   3   0   3.3   
40               Dāvis Bertāns     PF   24  SAS  23.523944  67   6  12.1   
41            Patrick Beverley     SG   28  HOU  23.745543  67  67  30.7   
42             Bismack Biyombo      C   24  ORL  28.010156  81  27  22.1   
43             Nemanja Bjelica     PF   28  MIN  24.464902  65   1  18.3   
44                 Tarik Black      C   25  LAL  26.787075  67  16  16.3   
45                Eric Bledsoe     PG   27  PHO  28.230813  66  66  33.0   
46               Joel Bolomboy     PF   23  UTA  25.179851  12   0   4.4   
47                Devin Booker     SG   20  PHO  24.425367  78  78  35.0   
48               Trevor Booker     PF   29  BRK  25.044375  71  43  24.7   
49               Avery Bradley     SG   26  BOS  22.496000  55  55  33.4   
50             Malcolm Brogdon     SG   24  MIL  27.152471  75  28  26.4   
51                Aaron Brooks     PG   32  IND  21.833140  65   0  13.8

In [29]:
pd.set_option("display.max_rows", None, "display.max_columns", None)
NBA_final_df

Player    Pos  Age   Tm        BMI   G  GS    MP  \
0                 Álex Abrines     SG   23  OKC  23.109796  68   6  15.5   
1                 Steven Adams      C   23  OKC  27.042386  80  80  29.9   
2                Arron Afflalo     SG   31  SAC  24.899646  61  45  25.9   
3                Alexis Ajinça      C   28  NOP  23.572742  39  15  15.0   
4                 Cole Aldrich      C   28  MIN  25.511685  62   0   8.6   
5            LaMarcus Aldridge     PF   31  SAS  25.511685  72  72  32.4   
6                  Lavoy Allen     PF   27  IND  27.858558  61   5  14.3   
7                   Tony Allen     SG   35  MEM  25.924342  71  66  27.0   
8              Al-Farouq Aminu     PF   26  POR  24.165625  61  25  29.1   
9               Chris Andersen      C   38  CLE  25.614961  12   0   9.5   
10               Alan Anderson     SF   34  LAC  25.420776  30   0  10.3   
11               Kyle Anderson     SF   23  SAS  24.644109  72  14  14.2   
12               Ryan Anderson     PF   28  HOU  25.715592  72  72  29.4   
13       Giannis Antetokounmpo     SF   22  MIL  24.695311  80  80  35.6   
14             Carmelo Anthony     SF   32  NYK  26.808845  74  74  34.3   
15                Joel Anthony      C   34  SAS  26.251334  19   0   6.4   
16                Trevor Ariza     SF   31  HOU  23.616406  80  80  34.7   
17              Darrell Arthur     PF   28  DEN  25.179851  41   7  15.6   
18                   Ömer Aşık      C   30  NOP  25.406037  31  19  15.5   
19               D.J. Augustin     PG   29  ORL  25.520532  78  20  19.7   
20                Luke Babbitt     SF   27  MIA  24.108368  68  55  15.7   
21                   Ron Baker     SG   23  NYK  26.776316  52  13  16.5   
22                Wade Baldwin     PG   20  MEM  24.342105  33   1  12.3   
23             Leandro Barbosa     SG   34  PHO  24.245689  67   0  14.4   
24                  J.J. Barea     PG   32  DAL  25.824490  35   6  22.0   
25             Harrison Barnes     PF   24  DAL  24.714844  79  79  35.5   
26                 Will Barton     SG   26  DEN  20.914366  60  19  28.4   
27                Brandon Bass     PF   31  LAC  27.460938  52   0  11.1   
28               Nicolas Batum     SG   28  CHO  25.264063  77  77  34.0   
29              Jerryd Bayless     PG   28  PHI  24.995556   3   1  23.7   
30                 Aron Baynes      C   30  DET  27.183224  75   2  15.5   
31               Kent Bazemore     SF   27  ATL  23.733553  73  64  26.9   
32                Bradley Beal     SG   23  WAS  25.870400  77  77  34.9   
33               Malik Beasley     SG   20  DEN  22.759868  22   1   7.5   
34             Michael Beasley     PF   28  MIL  25.179851  56   6  16.7   
35             Marco Belinelli     SG   30  CHO  26.085343  74   0  24.0   
36             DeAndre' Bembry     SF   22  ATL  24.899646  38   1   9.8   
37               Dragan Bender     PF   19  PHO  22.417092  43   0  13.3   
38             Anthony Bennett     PF   23  BRK  26.911719  23   1  11.5   
39                  Ben Bentil     PF   21  DAL  25.179851   3   0   3.3   
40               Dāvis Bertāns     PF   24  SAS  23.523944  67   6  12.1   
41            Patrick Beverley     SG   28  HOU  23.745543  67  67  30.7   
42             Bismack Biyombo      C   24  ORL  28.010156  81  27  22.1   
43             Nemanja Bjelica     PF   28  MIN  24.464902  65   1  18.3   
44                 Tarik Black      C   25  LAL  26.787075  67  16  16.3   
45                Eric Bledsoe     PG   27  PHO  28.230813  66  66  33.0   
46               Joel Bolomboy     PF   23  UTA  25.179851  12   0   4.4   
47                Devin Booker     SG   20  PHO  24.425367  78  78  35.0   
48               Trevor Booker     PF   29  BRK  25.044375  71  43  24.7   
49               Avery Bradley     SG   26  BOS  22.496000  55  55  33.4   
50             Malcolm Brogdon     SG   24  MIL  27.152471  75  28  26.4   
51                Aaron Brooks     PG   32  IND  21.833140  65   0  13.8

In [ ]:
NBA_final_df = NBA_final_df.drop(columns=['index'])

In [ ]:
NBA_final_df.dtypes

In [ ]:
sns.set(style='white')
sns.pairplot(NBA_final_df)

In [ ]:
NBA_final_df.info()

In [19]:
# import pickle
# df_pickle = '../data/NBA_stats_df.pk'
# var_to_pickle(NBA_final_df, df_pickle)

NameError: name 'var_to_pickle' is not defined

In [33]:
NBA_final_df.to_csv('player_data.csv',index=False)